In [1]:
import numpy as np
from scipy.spatial.distance import pdist, squareform
from matplotlib import pyplot as plt
from scipy.cluster.hierarchy import dendrogram, linkage

import plotly.offline as py
import plotly.graph_objs as go
from plotly.graph_objs import *
import plotly.figure_factory as FF

py.init_notebook_mode()

# Train Model

In [2]:
from gensim.models.ldamodel import LdaModel
from gensim.corpora import Dictionary, MmCorpus
import pandas as pd
import re
from gensim.parsing.preprocessing import remove_stopwords, strip_punctuation

Using TensorFlow backend.


In [5]:
df_fake = pd.read_csv('fake.csv')
df_fake[['title', 'text', 'language']].head()
df_fake = df_fake.loc[(pd.notnull(df_fake.text)) & (df_fake.language == 'english')]

# remove stopwords and punctuations
def preprocess(row):
    return strip_punctuation(remove_stopwords(row.lower()))
    
df_fake['text'] = df_fake['text'].apply(preprocess)

# Convert data to required input format by LDA
texts = []
for line in df_fake.text:
    lowered = line.lower()
    words = re.findall(r'\w+', lowered, flags = re.UNICODE | re.LOCALE)
    texts.append(words)
# Create a dictionary representation of the documents.
dictionary = Dictionary(texts)

# Filter out words that occur less than 2 documents, or more than 30% of the documents.
dictionary.filter_extremes(no_below=2, no_above=0.4)
# Bag-of-words representation of the documents.
corpus_fake = [dictionary.doc2bow(text) for text in texts]

In [12]:
lda_fake = LdaModel(corpus=corpus_fake, id2word=dictionary, num_topics=35, chunksize=1500, iterations=200, alpha='auto')

## Basic Dendrogram

In [13]:
from gensim.matutils import jenson_shannon

topic_dist = lda_fake.state.get_lambda()
def custom(X):
    return pdist(X, lambda u, v: jenson_shannon(u, v))
dendro = FF.create_dendrogram(topic_dist, distfun=custom, labels=range(1, 36))
dendro['layout'].update({'width':800, 'height':500})
py.iplot(dendro)

## Dendrogram with a Heatmap

In [23]:
from gensim.matutils import jenson_shannon

def js_dist(X):
    return pdist(X, lambda u, v: jenson_shannon(u, v))

topic_dist = lda_fake.state.get_lambda()

# Initialize figure by creating upper dendrogram
figure = FF.create_dendrogram(topic_dist, orientation='bottom', distfun=js_dist, labels=range(1, 36))
for i in range(len(figure['data'])):
    figure['data'][i]['yaxis'] = 'y2'

# Create Side Dendrogram
dendro_side = FF.create_dendrogram(topic_dist, orientation='right', distfun=js_dist)
for i in range(len(dendro_side['data'])):
    dendro_side['data'][i]['xaxis'] = 'x2'

# Add Side Dendrogram Data to Figure
figure['data'].extend(dendro_side['data'])

In [24]:
# Create Heatmap
dendro_leaves = dendro_side['layout']['yaxis']['ticktext']
dendro_leaves = list(map(int, dendro_leaves))
data_dist = pdist(topic_dist, lambda u, v: jenson_shannon(u, v))
heat_data = squareform(data_dist)
heat_data = heat_data[dendro_leaves,:]
heat_data = heat_data[:,dendro_leaves]

In [25]:
_, annotation = lda_fake.diff(lda_fake, distance="jenson_shannon")
annotation_html = [["+++ {}<br>--- {}".format(", ".join(int_tokens), 
                                          ", ".join(diff_tokens)) 
                        for (int_tokens, diff_tokens) in row] 
                       for row in annotation]
heatmap = go.Data([
    go.Heatmap(
        x = dendro_leaves,
        y = dendro_leaves,
        z = heat_data,
        colorscale = 'YIGnBu',
        text = annotation_html
    )
])

heatmap[0]['x'] = figure['layout']['xaxis']['tickvals']
heatmap[0]['y'] = dendro_side['layout']['yaxis']['tickvals']

# Add Heatmap Data to Figure
figure['data'].extend(go.Data(heatmap))

# Edit Layout
figure['layout'].update({'width':800, 'height':800,
                         'showlegend':False, 'hovermode': 'closest',
                         })


# Edit xaxis
figure['layout']['xaxis'].update({'domain': [.15, 1],
                                  'mirror': False,
                                  'showgrid': False,
                                  'showline': False,
                                  'zeroline': False,
                                  'ticks':""})
# Edit xaxis2
figure['layout'].update({'xaxis2': {'domain': [0, .15],
                                   'mirror': False,
                                   'showgrid': False,
                                   'showline': False,
                                   'zeroline': False,
                                   'showticklabels': False,
                                   'ticks':""}})

# Edit yaxis
figure['layout']['yaxis'].update({'domain': [0, .85],
                                  'mirror': False,
                                  'showgrid': False,
                                  'showline': False,
                                  'zeroline': False,
                                  'showticklabels': False,
                                  'ticks': ""})
# Edit yaxis2
figure['layout'].update({'yaxis2':{'domain':[.825, .975],
                                   'mirror': False,
                                   'showgrid': False,
                                   'showline': False,
                                   'zeroline': False,
                                   'showticklabels': False,
                                   'ticks':""}})

py.iplot(figure)

In [17]:
import pyLDAvis as ldavis
import pyLDAvis.gensim
ldavis.enable_notebook()

viz = ldavis.gensim.prepare(lda_fake, corpus_fake, dictionary, sort_topics=False)
viz

/Users/parul/.virtualenvs/gensim3/lib/python3.4/site-packages/pyLDAvis/_prepare.py:387: DeprecationWarning:


.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate_ix



PreparedData(topic_coordinates=            Freq  cluster  topics         x         y
topic                                                
0       0.888507        1       1 -0.047598  0.074505
1       7.050717        1       2  0.031477 -0.173816
2       1.855582        1       3 -0.152716  0.079753
3       7.287784        1       4  0.131770 -0.044570
4       2.219257        1       5  0.108020 -0.020772
5       2.182270        1       6  0.043379 -0.042086
6       2.084728        1       7  0.084242 -0.153063
7       1.786307        1       8 -0.061846  0.095362
8       1.991165        1       9 -0.026546 -0.009896
9       1.497030        1      10 -0.117518 -0.112498
10      3.868750        1      11 -0.078412 -0.043370
11      3.338144        1      12  0.001245  0.020873
12      1.427079        1      13 -0.140552 -0.168226
13      0.792857        1      14  0.053686 -0.049518
14      1.517094        1      15 -0.038649  0.109896
15      1.811666        1      16  0.041396  0.032072
16      0.805424        1      17 -0.011393  0.044791
17     13.219223        1      18  0.068354  0.082349
18      3.242676        1      19  0.079871  0.090788
19      2.348082        1      20  0.035405  0.116507
20      7.143653        1      21  0.142652 -0.015296
21      1.095749        1      22  0.080697 -0.025652
22      2.141270        1      23  0.069182 -0.068889
23      0.564230        1      24 -0.022977 -0.017130
24      2.168943        1      25 -0.204732  0.012515
25      2.017602        1      26 -0.131526 -0.048145
26      3.205468        1      27 -0.006358 -0.069383
27      1.331608        1      28 -0.028006 -0.046387
28      0.857302        1      29  0.069791 -0.032572
29      5.436044        1      30  0.012235  0.097244
30      2.576495        1      31  0.069808  0.122262
31      2.346154        1      32  0.031767  0.148504
32      1.648119        1      33 -0.227830  0.017618
33      4.920825        1      34  0.121816 -0.063808
34      1.332197        1      35  0.019865  0.060041, topic_info=      Category          Freq        Term         Total  loglift  logprob
term                                                                    
18435  Default  24975.000000       trump  24975.000000  30.0000  30.0000
6928   Default  23428.000000     clinton  23428.000000  29.0000  29.0000
18451  Default   8320.000000      russia   8320.000000  28.0000  28.0000
11834  Default   4895.000000         com   4895.000000  27.0000  27.0000
49842  Default  15147.000000     hillary  15147.000000  26.0000  26.0000
8007   Default   4918.000000       syria   4918.000000  25.0000  25.0000
25208  Default   5138.000000     russian   5138.000000  24.0000  24.0000
6677   Default   5970.000000         fbi   5970.000000  23.0000  23.0000
26163  Default   9737.000000    election   9737.000000  22.0000  22.0000
11947  Default   3236.000000       water   3236.000000  21.0000  21.0000
51664  Default  10036.000000       obama  10036.000000  20.0000  20.0000
31561  Default   4421.000000      emails   4421.000000  19.0000  19.0000
31388  Default   2420.000000      syrian   2420.000000  18.0000  18.0000
6260   Default   6570.000000         you   6570.000000  17.0000  17.0000
48791  Default   3089.000000      health   3089.000000  16.0000  16.0000
10667  Default  10104.000000           i  10104.000000  15.0000  15.0000
51339  Default   2047.000000      israel   2047.000000  14.0000  14.0000
19644  Default   2988.000000          al   2988.000000  13.0000  13.0000
15836  Default   6204.000000      donald   6204.000000  12.0000  12.0000
52494  Default   2462.000000       putin   2462.000000  11.0000  11.0000
1423   Default   7466.000000        news   7466.000000  10.0000  10.0000
3919   Default   9235.000000         war   9235.000000   9.0000   9.0000
52867  Default   1819.000000       saudi   1819.000000   8.0000   8.0000
44994  Default   5364.000000    military   5364.000000   7.0000   7.0000
45190  Default   8734.000000       media   8734.000000   6.00

In [18]:
def plot_difference(mdiff, title="", annotation=None):
    """
    Helper function for plot difference between models
    """
    annotation_html = None
    if annotation is not None:
        annotation_html = [["+++ {}<br>--- {}".format(", ".join(int_tokens), 
                                              ", ".join(diff_tokens)) 
                            for (int_tokens, diff_tokens) in row] 
                           for row in annotation]
        
    data = go.Heatmap(z=mdiff, colorscale='YIGnBu', text=annotation_html)
    layout = go.Layout(width=950, height=950, title=title,
                       xaxis=dict(title="topic"), yaxis=dict(title="topic"))
    py.iplot(dict(data=[data], layout=layout))

In [19]:
mdiff, annotation = lda_fake.diff(lda_fake, distance='jenson_shannon', num_words=50)
plot_difference(mdiff, title="Topic difference (one model) [jenson_shannon distance]", annotation=annotation)